ETL_australian_user_reviews.json

Importar Librerías 

In [1]:
import re
import ast
import json
import numpy as np
import pandas as pd
import pyarrow as pa
import pyarrow.parquet as pq
import nltk
from nltk.sentiment import SentimentIntensityAnalyzer

 Análisis de la base de datos
 Cargar Base de Datos

In [2]:
row = [] # creamos una lista vacia para ir agregando las filas del archivo json

with open ("Data/user_reviews.json", 'r', encoding='utf-8') as file: # abrimos el archivo json
    for line in file.readlines(): # leemos linea por linea
        row.append(ast.literal_eval(line)) # Utilizamos ast.literal_eval para interpretar la línea como expresión literal de Python


reviews = pd.DataFrame(row)
reviews

user_id                                           user_url  \
0      76561197970982479  http://steamcommunity.com/profiles/76561197970...   
1                js41637               http://steamcommunity.com/id/js41637   
2              evcentric             http://steamcommunity.com/id/evcentric   
3                  doctr                 http://steamcommunity.com/id/doctr   
4              maplemage             http://steamcommunity.com/id/maplemage   
...                  ...                                                ...   
25794  76561198306599751  http://steamcommunity.com/profiles/76561198306...   
25795           Ghoustik              http://steamcommunity.com/id/Ghoustik   
25796  76561198310819422  http://steamcommunity.com/profiles/76561198310...   
25797  76561198312638244  http://steamcommunity.com/profiles/76561198312...   
25798        LydiaMorley           http://steamcommunity.com/id/LydiaMorley   

                                                 reviews  
0      [{'funny': '', 'posted': 'Posted November 5, 2...  
1      [{'funny': '', 'posted': 'Posted June 24, 2014...  
2      [{'funny': '', 'posted': 'Posted February 3.',...  
3      [{'funny': '', 'posted': 'Posted October 14, 2...  
4      [{'funny': '3 people found this review funny',...  
...                                                  ...  
25794  [{'funny': '', 'posted': 'Posted May 31.', 'la...  
25795  [{'funny': '', 'posted': 'Posted June 17.', 'l...  
25796  [{'funny': '1 person found this review funny',...  
25797  [{'funny': '', 'posted': 'Posted July 21.', 'l...  
25798  [{'funny': '1 person found this review funny',...  

[25799 rows x 3 columns]

Usamos el metodo explode para separar los "reviews"

In [3]:
editado = reviews.explode('reviews') # Utilizamos el metodo explode para separar los reviews de cada juego
editado.head() 

user_id                                           user_url  \
0  76561197970982479  http://steamcommunity.com/profiles/76561197970...   
0  76561197970982479  http://steamcommunity.com/profiles/76561197970...   
0  76561197970982479  http://steamcommunity.com/profiles/76561197970...   
1            js41637               http://steamcommunity.com/id/js41637   
1            js41637               http://steamcommunity.com/id/js41637   

                                             reviews  
0  {'funny': '', 'posted': 'Posted November 5, 20...  
0  {'funny': '', 'posted': 'Posted July 15, 2011....  
0  {'funny': '', 'posted': 'Posted April 21, 2011...  
1  {'funny': '', 'posted': 'Posted June 24, 2014....  
1  {'funny': '', 'posted': 'Posted September 8, 2...

Normalización de datos utilizamos json_normalize

In [4]:
normalizado = pd.json_normalize(editado['reviews'].dropna()) # Utilizamos el metodo json_normalize para normalizar los datos
normalizado

funny                     posted  \
0                                         Posted November 5, 2011.   
1                                            Posted July 15, 2011.   
2                                           Posted April 21, 2011.   
3                                            Posted June 24, 2014.   
4                                        Posted September 8, 2013.   
...                                 ...                        ...   
59300                                              Posted July 10.   
59301                                               Posted July 8.   
59302  1 person found this review funny             Posted July 3.   
59303                                              Posted July 20.   
59304                                               Posted July 2.   

      last_edited item_id                                          helpful  \
0                    1250                                   No ratings yet   
1                   22200                                   No ratings yet   
2                   43110                                   No ratings yet   
3                  251610  15 of 20 people (75%) found this review helpful   
4                  227300     0 of 1 people (0%) found this review helpful   
...           ...     ...                                              ...   
59300                  70                                   No ratings yet   
59301              362890                                   No ratings yet   
59302              273110    1 of 2 people (50%) found this review helpful   
59303                 730                                   No ratings yet   
59304                 440                                   No ratings yet   

       recommend                                             review  
0           True  Simple yet with great replayability. In my opi...  
1           True               It's unique and worth a playthrough.  
2           True  Great atmosphere. The gunplay can be a bit chu...  
3           True  I know what you think when you see this title ...  
4           True  For a simple (it's actually not all that simpl...  
...          ...                                                ...  
59300       True  a must have classic from steam definitely wort...  
59301       True  this game is a perfect remake of the original ...  
59302       True  had so much fun plaing this and collecting res...  
59303       True                                                 :D  
59304       True                                     so much fun :D  

[59305 rows x 7 columns]

In [5]:
normalizado.reset_index(inplace=True) # Reseteamos el index para que no se repita
normalizado

index                             funny                     posted  \
0          0                                     Posted November 5, 2011.   
1          1                                        Posted July 15, 2011.   
2          2                                       Posted April 21, 2011.   
3          3                                        Posted June 24, 2014.   
4          4                                    Posted September 8, 2013.   
...      ...                               ...                        ...   
59300  59300                                              Posted July 10.   
59301  59301                                               Posted July 8.   
59302  59302  1 person found this review funny             Posted July 3.   
59303  59303                                              Posted July 20.   
59304  59304                                               Posted July 2.   

      last_edited item_id                                          helpful  \
0                    1250                                   No ratings yet   
1                   22200                                   No ratings yet   
2                   43110                                   No ratings yet   
3                  251610  15 of 20 people (75%) found this review helpful   
4                  227300     0 of 1 people (0%) found this review helpful   
...           ...     ...                                              ...   
59300                  70                                   No ratings yet   
59301              362890                                   No ratings yet   
59302              273110    1 of 2 people (50%) found this review helpful   
59303                 730                                   No ratings yet   
59304                 440                                   No ratings yet   

       recommend                                             review  
0           True  Simple yet with great replayability. In my opi...  
1           True               It's unique and worth a playthrough.  
2           True  Great atmosphere. The gunplay can be a bit chu...  
3           True  I know what you think when you see this title ...  
4           True  For a simple (it's actually not all that simpl...  
...          ...                                                ...  
59300       True  a must have classic from steam definitely wort...  
59301       True  this game is a perfect remake of the original ...  
59302       True  had so much fun plaing this and collecting res...  
59303       True                                                 :D  
59304       True                                     so much fun :D  

[59305 rows x 8 columns]

In [6]:
editado.reset_index(inplace=True)
editado

index            user_id  \
0          0  76561197970982479   
1          0  76561197970982479   
2          0  76561197970982479   
3          1            js41637   
4          1            js41637   
...      ...                ...   
59328  25797  76561198312638244   
59329  25797  76561198312638244   
59330  25798        LydiaMorley   
59331  25798        LydiaMorley   
59332  25798        LydiaMorley   

                                                user_url  \
0      http://steamcommunity.com/profiles/76561197970...   
1      http://steamcommunity.com/profiles/76561197970...   
2      http://steamcommunity.com/profiles/76561197970...   
3                   http://steamcommunity.com/id/js41637   
4                   http://steamcommunity.com/id/js41637   
...                                                  ...   
59328  http://steamcommunity.com/profiles/76561198312...   
59329  http://steamcommunity.com/profiles/76561198312...   
59330           http://steamcommunity.com/id/LydiaMorley   
59331           http://steamcommunity.com/id/LydiaMorley   
59332           http://steamcommunity.com/id/LydiaMorley   

                                                 reviews  
0      {'funny': '', 'posted': 'Posted November 5, 20...  
1      {'funny': '', 'posted': 'Posted July 15, 2011....  
2      {'funny': '', 'posted': 'Posted April 21, 2011...  
3      {'funny': '', 'posted': 'Posted June 24, 2014....  
4      {'funny': '', 'posted': 'Posted September 8, 2...  
...                                                  ...  
59328  {'funny': '', 'posted': 'Posted July 10.', 'la...  
59329  {'funny': '', 'posted': 'Posted July 8.', 'las...  
59330  {'funny': '1 person found this review funny', ...  
59331  {'funny': '', 'posted': 'Posted July 20.', 'la...  
59332  {'funny': '', 'posted': 'Posted July 2.', 'las...  

[59333 rows x 4 columns]

Conactenamos los dos DataFrames y elimino la columna reviews

In [7]:
reviews_ok = pd.concat([editado, normalizado], axis=1) # Concatenamos los dos dataframes
reviews_ok = reviews_ok.drop(columns = ['reviews']) # Eliminamos la columna reviews
reviews_ok

C:\Users\Usuario\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\IPython\lib\pretty.py:778: FutureWarning: In a future version, object-dtype columns with all-bool values will not be included in reductions with bool_only=True. Explicitly cast to bool dtype instead.
  output = repr(obj)
C:\Users\Usuario\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\IPython\core\formatters.py:344: FutureWarning: In a future version, object-dtype columns with all-bool values will not be included in reductions with bool_only=True. Explicitly cast to bool dtype instead.
  return method()


index            user_id  \
0          0  76561197970982479   
1          0  76561197970982479   
2          0  76561197970982479   
3          1            js41637   
4          1            js41637   
...      ...                ...   
59328  25797  76561198312638244   
59329  25797  76561198312638244   
59330  25798        LydiaMorley   
59331  25798        LydiaMorley   
59332  25798        LydiaMorley   

                                                user_url  index funny  \
0      http://steamcommunity.com/profiles/76561197970...    0.0         
1      http://steamcommunity.com/profiles/76561197970...    1.0         
2      http://steamcommunity.com/profiles/76561197970...    2.0         
3                   http://steamcommunity.com/id/js41637    3.0         
4                   http://steamcommunity.com/id/js41637    4.0         
...                                                  ...    ...   ...   
59328  http://steamcommunity.com/profiles/76561198312...    NaN   NaN   
59329  http://steamcommunity.com/profiles/76561198312...    NaN   NaN   
59330           http://steamcommunity.com/id/LydiaMorley    NaN   NaN   
59331           http://steamcommunity.com/id/LydiaMorley    NaN   NaN   
59332           http://steamcommunity.com/id/LydiaMorley    NaN   NaN   

                          posted last_edited item_id  \
0       Posted November 5, 2011.                1250   
1          Posted July 15, 2011.               22200   
2         Posted April 21, 2011.               43110   
3          Posted June 24, 2014.              251610   
4      Posted September 8, 2013.              227300   
...                          ...         ...     ...   
59328                        NaN         NaN     NaN   
59329                        NaN         NaN     NaN   
59330                        NaN         NaN     NaN   
59331                        NaN         NaN     NaN   
59332                        NaN         NaN     NaN   

                                               helpful recommend  \
0                                       No ratings yet      True   
1                                       No ratings yet      True   
2                                       No ratings yet      True   
3      15 of 20 people (75%) found this review helpful      True   
4         0 of 1 people (0%) found this review helpful      True   
...                                                ...       ...   
59328                                              NaN       NaN   
59329                                              NaN       NaN   
59330                                              NaN       NaN   
59331                                              NaN       NaN   
59332                                              NaN       NaN   

                                                  review  
0      Simple yet with great replayability. In my opi...  
1                   It's unique and worth a playthrough.  
2      Great atmosphere. The gunplay can be a bit chu...  
3      I know what you think when you see this title ...  
4      For a simple (it's actually not all that simpl...  
...                                                  ...  
59328                                                NaN  
59329                                                NaN  
59330                                                NaN  
59331                                                NaN  
59332                                                NaN  

[59333 rows x 11 columns]

Elimino la columna "index"

In [8]:
reviews_ok = reviews_ok.drop(columns="index") # Eliminamos la columna index
reviews_ok

C:\Users\Usuario\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\IPython\lib\pretty.py:778: FutureWarning: In a future version, object-dtype columns with all-bool values will not be included in reductions with bool_only=True. Explicitly cast to bool dtype instead.
  output = repr(obj)
C:\Users\Usuario\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\IPython\core\formatters.py:344: FutureWarning: In a future version, object-dtype columns with all-bool values will not be included in reductions with bool_only=True. Explicitly cast to bool dtype instead.
  return method()


user_id                                           user_url  \
0      76561197970982479  http://steamcommunity.com/profiles/76561197970...   
1      76561197970982479  http://steamcommunity.com/profiles/76561197970...   
2      76561197970982479  http://steamcommunity.com/profiles/76561197970...   
3                js41637               http://steamcommunity.com/id/js41637   
4                js41637               http://steamcommunity.com/id/js41637   
...                  ...                                                ...   
59328  76561198312638244  http://steamcommunity.com/profiles/76561198312...   
59329  76561198312638244  http://steamcommunity.com/profiles/76561198312...   
59330        LydiaMorley           http://steamcommunity.com/id/LydiaMorley   
59331        LydiaMorley           http://steamcommunity.com/id/LydiaMorley   
59332        LydiaMorley           http://steamcommunity.com/id/LydiaMorley   

      funny                     posted last_edited item_id  \
0             Posted November 5, 2011.                1250   
1                Posted July 15, 2011.               22200   
2               Posted April 21, 2011.               43110   
3                Posted June 24, 2014.              251610   
4            Posted September 8, 2013.              227300   
...     ...                        ...         ...     ...   
59328   NaN                        NaN         NaN     NaN   
59329   NaN                        NaN         NaN     NaN   
59330   NaN                        NaN         NaN     NaN   
59331   NaN                        NaN         NaN     NaN   
59332   NaN                        NaN         NaN     NaN   

                                               helpful recommend  \
0                                       No ratings yet      True   
1                                       No ratings yet      True   
2                                       No ratings yet      True   
3      15 of 20 people (75%) found this review helpful      True   
4         0 of 1 people (0%) found this review helpful      True   
...                                                ...       ...   
59328                                              NaN       NaN   
59329                                              NaN       NaN   
59330                                              NaN       NaN   
59331                                              NaN       NaN   
59332                                              NaN       NaN   

                                                  review  
0      Simple yet with great replayability. In my opi...  
1                   It's unique and worth a playthrough.  
2      Great atmosphere. The gunplay can be a bit chu...  
3      I know what you think when you see this title ...  
4      For a simple (it's actually not all that simpl...  
...                                                  ...  
59328                                                NaN  
59329                                                NaN  
59330                                                NaN  
59331                                                NaN  
59332                                                NaN  

[59333 rows x 9 columns]

In [9]:
tipo_data = {"columna":[],"tipos_de_datos":[]} # Creamos un diccionario vacio

for columna in reviews_ok.columns: # Recorremos las columnas del dataframe
    tipo_data["columna"].append(columna) # Agregamos el nombre de la columna
    tipo_data["tipos_de_datos"].append(reviews_ok[columna].apply(type).unique()) # Agregamos el tipo de dato de la columna

analisis= pd.DataFrame(tipo_data) # Creamos un dataframe con el diccionario
analisis

columna                     tipos_de_datos
0      user_id                    [<class 'str'>]
1     user_url                    [<class 'str'>]
2        funny   [<class 'str'>, <class 'float'>]
3       posted   [<class 'str'>, <class 'float'>]
4  last_edited   [<class 'str'>, <class 'float'>]
5      item_id   [<class 'str'>, <class 'float'>]
6      helpful   [<class 'str'>, <class 'float'>]
7    recommend  [<class 'bool'>, <class 'float'>]
8       review   [<class 'str'>, <class 'float'>]

Tras aplicar el proceso de normalización a los datos, se identificó la presencia de valores nulos en el conjunto de datos. Debido al tamaño significativo del dataframe y con el objetivo de mantener la integridad y consistencia de los datos para un análisis preciso, se tomó la decisión de eliminar las filas que contenían valores nulos. Esta acción permitira mantener la calidad de los datos y garantizar la fiabilidad de los resultados en las etapas posteriores del análisis

Busqueda de duplicados 

In [10]:
duplicados = reviews_ok.loc[reviews_ok.duplicated()] # Buscamos los duplicados
duplicados

user_id                                           user_url  \
1112          bobseagull            http://steamcommunity.com/id/bobseagull   
2894          ImSeriouss            http://steamcommunity.com/id/ImSeriouss   
2895          ImSeriouss            http://steamcommunity.com/id/ImSeriouss   
2896          ImSeriouss            http://steamcommunity.com/id/ImSeriouss   
3582   76561198062039159  http://steamcommunity.com/profiles/76561198062...   
...                  ...                                                ...   
59327  76561198312638244  http://steamcommunity.com/profiles/76561198312...   
59328  76561198312638244  http://steamcommunity.com/profiles/76561198312...   
59329  76561198312638244  http://steamcommunity.com/profiles/76561198312...   
59331        LydiaMorley           http://steamcommunity.com/id/LydiaMorley   
59332        LydiaMorley           http://steamcommunity.com/id/LydiaMorley   

      funny                      posted last_edited item_id  \
1112         Posted September 24, 2015.              346110   
2894           Posted January 13, 2014.              211820   
2895           Posted January 10, 2014.                 440   
2896             Posted March 19, 2012.               42680   
3582          Posted December 11, 2015.                 730   
...     ...                         ...         ...     ...   
59327   NaN                         NaN         NaN     NaN   
59328   NaN                         NaN         NaN     NaN   
59329   NaN                         NaN         NaN     NaN   
59331   NaN                         NaN         NaN     NaN   
59332   NaN                         NaN         NaN     NaN   

                                              helpful recommend  \
1112   1 of 1 people (100%) found this review helpful      True   
2894                                   No ratings yet      True   
2895                                   No ratings yet      True   
2896                                   No ratings yet      True   
3582     0 of 1 people (0%) found this review helpful      True   
...                                               ...       ...   
59327                                             NaN       NaN   
59328                                             NaN       NaN   
59329                                             NaN       NaN   
59331                                             NaN       NaN   
59332                                             NaN       NaN   

                                                  review  
1112                                                 yep  
2894   If you want to play this game.. expect glithes...  
2895   Really good game! fun! Good for people who wan...  
2896      Good but a bit overdone. Still love it though.  
3582                               I rate it R8/Revolver  
...                                                  ...  
59327                                                NaN  
59328                                                NaN  
59329                                                NaN  
59331                                                NaN  
59332                                                NaN  

[154 rows x 9 columns]

Eliminación de duplicados 

In [11]:
reviews_ok = reviews_ok.drop_duplicates(keep='first') # Eliminamos los duplicados
reviews_ok

user_id                                           user_url  \
0      76561197970982479  http://steamcommunity.com/profiles/76561197970...   
1      76561197970982479  http://steamcommunity.com/profiles/76561197970...   
2      76561197970982479  http://steamcommunity.com/profiles/76561197970...   
3                js41637               http://steamcommunity.com/id/js41637   
4                js41637               http://steamcommunity.com/id/js41637   
...                  ...                                                ...   
59323  76561198306599751  http://steamcommunity.com/profiles/76561198306...   
59324           Ghoustik              http://steamcommunity.com/id/Ghoustik   
59325  76561198310819422  http://steamcommunity.com/profiles/76561198310...   
59326  76561198312638244  http://steamcommunity.com/profiles/76561198312...   
59330        LydiaMorley           http://steamcommunity.com/id/LydiaMorley   

      funny                     posted last_edited item_id  \
0             Posted November 5, 2011.                1250   
1                Posted July 15, 2011.               22200   
2               Posted April 21, 2011.               43110   
3                Posted June 24, 2014.              251610   
4            Posted September 8, 2013.              227300   
...     ...                        ...         ...     ...   
59323   NaN                        NaN         NaN     NaN   
59324   NaN                        NaN         NaN     NaN   
59325   NaN                        NaN         NaN     NaN   
59326   NaN                        NaN         NaN     NaN   
59330   NaN                        NaN         NaN     NaN   

                                               helpful recommend  \
0                                       No ratings yet      True   
1                                       No ratings yet      True   
2                                       No ratings yet      True   
3      15 of 20 people (75%) found this review helpful      True   
4         0 of 1 people (0%) found this review helpful      True   
...                                                ...       ...   
59323                                              NaN       NaN   
59324                                              NaN       NaN   
59325                                              NaN       NaN   
59326                                              NaN       NaN   
59330                                              NaN       NaN   

                                                  review  
0      Simple yet with great replayability. In my opi...  
1                   It's unique and worth a playthrough.  
2      Great atmosphere. The gunplay can be a bit chu...  
3      I know what you think when you see this title ...  
4      For a simple (it's actually not all that simpl...  
...                                                  ...  
59323                                                NaN  
59324                                                NaN  
59325                                                NaN  
59326                                                NaN  
59330                                                NaN  

[59179 rows x 9 columns]

Realice una búsqueda de los valores Nulos 

In [12]:
nulos = reviews_ok.isnull().sum() # Buscamos los nulos
nulos

user_id         0
user_url        0
funny          18
posted         18
last_edited    18
item_id        18
helpful        18
recommend      18
review         18
dtype: int64

Eliminación de valores Nulos 

In [13]:
reviews_ok = reviews_ok.dropna().reset_index(drop=True) # Eliminamos los nulos
reviews_ok

user_id  \
0         76561197970982479   
1         76561197970982479   
2         76561197970982479   
3                   js41637   
4                   js41637   
...                     ...   
59156  Fuckfhaisjnsnsjakaka   
59157            3214213216   
59158          ChrisCoroner   
59159      CaptainAmericaCw   
59160     76561198267374962   

                                                user_url  \
0      http://steamcommunity.com/profiles/76561197970...   
1      http://steamcommunity.com/profiles/76561197970...   
2      http://steamcommunity.com/profiles/76561197970...   
3                   http://steamcommunity.com/id/js41637   
4                   http://steamcommunity.com/id/js41637   
...                                                  ...   
59156  http://steamcommunity.com/id/Fuckfhaisjnsnsjakaka   
59157            http://steamcommunity.com/id/3214213216   
59158          http://steamcommunity.com/id/ChrisCoroner   
59159      http://steamcommunity.com/id/CaptainAmericaCw   
59160  http://steamcommunity.com/profiles/76561198267...   

                                  funny                     posted  \
0                                         Posted November 5, 2011.   
1                                            Posted July 15, 2011.   
2                                           Posted April 21, 2011.   
3                                            Posted June 24, 2014.   
4                                        Posted September 8, 2013.   
...                                 ...                        ...   
59156                                              Posted July 10.   
59157                                               Posted July 8.   
59158  1 person found this review funny             Posted July 3.   
59159                                              Posted July 20.   
59160                                               Posted July 2.   

      last_edited item_id                                          helpful  \
0                    1250                                   No ratings yet   
1                   22200                                   No ratings yet   
2                   43110                                   No ratings yet   
3                  251610  15 of 20 people (75%) found this review helpful   
4                  227300     0 of 1 people (0%) found this review helpful   
...           ...     ...                                              ...   
59156                  70                                   No ratings yet   
59157              362890                                   No ratings yet   
59158              273110    1 of 2 people (50%) found this review helpful   
59159                 730                                   No ratings yet   
59160                 440                                   No ratings yet   

      recommend                                             review  
0          True  Simple yet with great replayability. In my opi...  
1          True               It's unique and worth a playthrough.  
2          True  Great atmosphere. The gunplay can be a bit chu...  
3          True  I know what you think when you see this title ...  
4          True  For a simple (it's actually not all that simpl...  
...         ...                                                ...  
59156      True  a must have classic from steam definitely wort...  
59157      True  this game is a perfect remake of the original ...  
59158      True  had so much fun plaing this and collecting res...  
59159      True                                                 :D  
59160      True                                     so much fun :D  

[59161 rows x 9 columns]

La columna "posted" alberga datos que representan fechas en formato de cadena de texto. Por este motivo, se lleva a cabo la conversión de dichos datos al formato de fecha y hora (datetime).

In [14]:
reviews_ok['posted'] = reviews_ok['posted'].str.extract(r'Posted ([\w\s\d,]+)') # Utilizamos regex para extraer la fecha
reviews_ok.head()

user_id                                           user_url funny  \
0  76561197970982479  http://steamcommunity.com/profiles/76561197970...         
1  76561197970982479  http://steamcommunity.com/profiles/76561197970...         
2  76561197970982479  http://steamcommunity.com/profiles/76561197970...         
3            js41637               http://steamcommunity.com/id/js41637         
4            js41637               http://steamcommunity.com/id/js41637         

              posted last_edited item_id  \
0   November 5, 2011                1250   
1      July 15, 2011               22200   
2     April 21, 2011               43110   
3      June 24, 2014              251610   
4  September 8, 2013              227300   

                                           helpful recommend  \
0                                   No ratings yet      True   
1                                   No ratings yet      True   
2                                   No ratings yet      True   
3  15 of 20 people (75%) found this review helpful      True   
4     0 of 1 people (0%) found this review helpful      True   

                                              review  
0  Simple yet with great replayability. In my opi...  
1               It's unique and worth a playthrough.  
2  Great atmosphere. The gunplay can be a bit chu...  
3  I know what you think when you see this title ...  
4  For a simple (it's actually not all that simpl...

In [15]:
reviews_ok['posted'] = reviews_ok['posted'].replace({'Posted': ''}, regex=True) # Eliminamos la palabra Posted
reviews_ok.head()

user_id                                           user_url funny  \
0  76561197970982479  http://steamcommunity.com/profiles/76561197970...         
1  76561197970982479  http://steamcommunity.com/profiles/76561197970...         
2  76561197970982479  http://steamcommunity.com/profiles/76561197970...         
3            js41637               http://steamcommunity.com/id/js41637         
4            js41637               http://steamcommunity.com/id/js41637         

              posted last_edited item_id  \
0   November 5, 2011                1250   
1      July 15, 2011               22200   
2     April 21, 2011               43110   
3      June 24, 2014              251610   
4  September 8, 2013              227300   

                                           helpful recommend  \
0                                   No ratings yet      True   
1                                   No ratings yet      True   
2                                   No ratings yet      True   
3  15 of 20 people (75%) found this review helpful      True   
4     0 of 1 people (0%) found this review helpful      True   

                                              review  
0  Simple yet with great replayability. In my opi...  
1               It's unique and worth a playthrough.  
2  Great atmosphere. The gunplay can be a bit chu...  
3  I know what you think when you see this title ...  
4  For a simple (it's actually not all that simpl...

In [16]:
reviews_ok['posted'] = pd.to_datetime(reviews_ok['posted'], errors='coerce') # Convertimos la columna posted a datetime
reviews_ok.head()

user_id                                           user_url funny  \
0  76561197970982479  http://steamcommunity.com/profiles/76561197970...         
1  76561197970982479  http://steamcommunity.com/profiles/76561197970...         
2  76561197970982479  http://steamcommunity.com/profiles/76561197970...         
3            js41637               http://steamcommunity.com/id/js41637         
4            js41637               http://steamcommunity.com/id/js41637         

      posted last_edited item_id  \
0 2011-11-05                1250   
1 2011-07-15               22200   
2 2011-04-21               43110   
3 2014-06-24              251610   
4 2013-09-08              227300   

                                           helpful recommend  \
0                                   No ratings yet      True   
1                                   No ratings yet      True   
2                                   No ratings yet      True   
3  15 of 20 people (75%) found this review helpful      True   
4     0 of 1 people (0%) found this review helpful      True   

                                              review  
0  Simple yet with great replayability. In my opi...  
1               It's unique and worth a playthrough.  
2  Great atmosphere. The gunplay can be a bit chu...  
3  I know what you think when you see this title ...  
4  For a simple (it's actually not all that simpl...

In [17]:
reviews_ok["posted"].isnull().sum() # Contamos los valores nulos de la columna posted

10091

In [18]:
reviews_ok["posted"].max() # Buscamos la fecha maxima

Timestamp('2015-12-31 00:00:00')

In [19]:
reviews_ok["posted"].min() # Buscamos la fecha minima

Timestamp('2010-10-16 00:00:00')

In [20]:
from datetime import datetime

In [21]:
# Definimos un rango temporal adecuado para el conjunto de datos
start_date = datetime(2010, 10, 16)
end_date = datetime(2015, 12, 31)

In [23]:
# Imputamos fechas aleatorias a las filas con valores nulos en 'posted'
reviews_ok.loc[reviews_ok['posted'].isnull(), 'posted'] = np.random.choice(pd.date_range(start_date, end_date), reviews_ok['posted'].isnull().sum())

In [24]:
reviews_ok["posted"].isnull().sum() # Revisamos nuevamente la cantidad de valores nulos de la columna posted

0

In [25]:
# Extraemos el año de la columna "release_date" y creamos una nueva columna llamada "release_year"
reviews_ok["posted_year"] = reviews_ok["posted"].dt.year 
reviews_ok.head(2)

user_id                                           user_url funny  \
0  76561197970982479  http://steamcommunity.com/profiles/76561197970...         
1  76561197970982479  http://steamcommunity.com/profiles/76561197970...         

      posted last_edited item_id         helpful recommend  \
0 2011-11-05                1250  No ratings yet      True   
1 2011-07-15               22200  No ratings yet      True   

                                              review  posted_year  
0  Simple yet with great replayability. In my opi...         2011  
1               It's unique and worth a playthrough.         2011

Crear la columna ***'sentiment_analysis'*** aplicando análisis de sentimiento con NLP con la siguiente escala: debe tomar el valor '0' si es malo, '1' si es neutral y '2' si es positivo. Esta nueva columna debe reemplazar la de user_reviews.review para facilitar el trabajo de los modelos de machine learning y el análisis de datos. De no ser posible este análisis por estar ausente la reseña escrita, debe tomar el valor de `1`.

In [26]:
def analizar_sentimiento_nltk(review):
    if review is None:
        return 1

    # Analizamos el sentimiento con SentimentIntensityAnalyzer
    analyzer = SentimentIntensityAnalyzer()
    sentiment_score = analyzer.polarity_scores(review)['compound']

    # Ajustamos los umbrales para clasificar el sentimiento
    if sentiment_score > 0.4:
        return 2  # Positivo
    elif sentiment_score < -0.5:
        return 0  # Negativo
    else:
        return 1  # Neutral

In [27]:
# Aplicamos la función a la columna review
reviews_ok["sentiment_analysis"] = reviews_ok["review"].astype(str).apply(analizar_sentimiento_nltk)
reviews_ok.head(5)

user_id                                           user_url funny  \
0  76561197970982479  http://steamcommunity.com/profiles/76561197970...         
1  76561197970982479  http://steamcommunity.com/profiles/76561197970...         
2  76561197970982479  http://steamcommunity.com/profiles/76561197970...         
3            js41637               http://steamcommunity.com/id/js41637         
4            js41637               http://steamcommunity.com/id/js41637         

      posted last_edited item_id  \
0 2011-11-05                1250   
1 2011-07-15               22200   
2 2011-04-21               43110   
3 2014-06-24              251610   
4 2013-09-08              227300   

                                           helpful recommend  \
0                                   No ratings yet      True   
1                                   No ratings yet      True   
2                                   No ratings yet      True   
3  15 of 20 people (75%) found this review helpful      True   
4     0 of 1 people (0%) found this review helpful      True   

                                              review  posted_year  \
0  Simple yet with great replayability. In my opi...         2011   
1               It's unique and worth a playthrough.         2011   
2  Great atmosphere. The gunplay can be a bit chu...         2011   
3  I know what you think when you see this title ...         2014   
4  For a simple (it's actually not all that simpl...         2013   

   sentiment_analysis  
0                   2  
1                   1  
2                   2  
3                   2  
4                   2

In [97]:
reviews_ok["sentiment_analysis"].value_counts() # Hacemos un conteo de los sentimientos

2    32181
1    22000
0     4980
Name: sentiment_analysis, dtype: int64

In [98]:
reviews_ok["review"][2548] # Revisamos el review 2548

'One of those games that worth to play'

In [99]:
reviews_ok["sentiment_analysis"][2548] # Revisamos el sentimiento del review 2548 para comparar

2

In [100]:
# Revisamos los reviews con sentimiento positivo para tener una idea de que tan bien funciona el analisis de sentimientos
for i in range(len(reviews_ok["sentiment_analysis"])):    
    if reviews_ok["sentiment_analysis"][i] == 2:
        print(reviews_ok["review"][i])

Simple yet with great replayability. In my opinion does "zombie" hordes and team work better than left 4 dead plus has a global leveling system. Alot of down to earth "zombie" splattering fun for the whole family. Amazed this sort of FPS is so rare.
Great atmosphere. The gunplay can be a bit chunky at times but at the end of the day this game is definitely worth it and I hope they do a sequel...so buy the game so I get a sequel!
I know what you think when you see this title "Barbie Dreamhouse Party" but do not be intimidated by it's title, this is easily one of my GOTYs. You don't get any of that cliche game mechanics that all the latest games have, this is simply good core gameplay. Yes, you can't 360 noscope your friends, but what you can do is show them up with your bad ♥♥♥ dance moves and put them to shame as you show them what true fashion and color combinations are.I know this game says for kids but, this is easily for any age range and any age will have a blast playing this.8/8


In [101]:
reviews_ok = reviews_ok.drop(columns=["review"])
reviews_ok.columns

Index(['user_id', 'user_url', 'funny', 'posted', 'last_edited', 'item_id',
       'helpful', 'recommend', 'posted_year', 'sentiment_analysis'],
      dtype='object')

In [102]:
reviews_ok.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 59161 entries, 0 to 59160
Data columns (total 10 columns):
 #   Column              Non-Null Count  Dtype         
---  ------              --------------  -----         
 0   user_id             59161 non-null  object        
 1   user_url            59161 non-null  object        
 2   funny               59161 non-null  object        
 3   posted              59161 non-null  datetime64[ns]
 4   last_edited         59161 non-null  object        
 5   item_id             59161 non-null  object        
 6   helpful             59161 non-null  object        
 7   recommend           59161 non-null  object        
 8   posted_year         59161 non-null  int64         
 9   sentiment_analysis  59161 non-null  int64         
dtypes: datetime64[ns](1), int64(2), object(7)
memory usage: 4.5+ MB


In [103]:
# Eliminamos las columnas 'funny', 'last_edited' y 'helpful'
reviews_ok = reviews_ok.drop(columns=["funny", "last_edited", "helpful"])

In [104]:
# Eliminamos la columna 'user_url'
reviews_ok = reviews_ok.drop(columns=["user_url"])

Guardamos el DataFrame en formato Parquet para aprovechar sus ventajas en términos de eficiencia de almacenamiento y procesamiento de datos. El formato Parquet es altamente eficiente en la compresión y almacenamiento de datos, lo que resulta beneficioso para conjuntos de datos extensos como el que estamos manejando.

Creamos una copia del Dataframe 

In [105]:
reviews_ok = reviews_ok.copy() # Creamos una copia del dataframe

Exportamos el DataFrame a un archivo csv 

In [107]:
reviews_ok.to_csv("Data/australian_user_reviews.csv", index=False, encoding='utf-8') # Exportamos el dataframe a csv

Leemos el archivo csv 

In [109]:
reviews_ok = pd.read_csv("Data/australian_user_reviews.csv") # leemos el archivo csv


Exportamos la tabla a un archivo Parquet

In [110]:
tabla = pa.Table.from_pandas(reviews_ok) # convertimos el dataframe en una tabla de pyarrow
pq.write_table(tabla,"Data/australian_user_reviews.parquet") # exportamos la tabla a parquet